# Menu
1. [Import Libraries, .env Variables, and Define Config Variables](#import-libraries-env-variables-and-define-config-variables)
2. [Data Loading](#data-loading)
3. [Checking Correlation Heatmap and Boxplot of Numerical Columns](#checking-correlation-heatmap-and-boxplot-of-numerical-columns)
4. [Data Preprocessing](#data-preprocessing)
5. [Feature Engineering](#feature-engineering)
6. [Choosing Features](#choosing-features)
7. [Model Evaluation](#model-evaluation)
    - a) [Train CatBoost Classifier](#catboost-classifier)
    - b) [Train Random Forest Classifier](#randomforest-classifier)
8. [Choosing the Best Model and Saving Model](#choosing-best-model-and-saving-model)



# Import Libraries, .env Variables and define config variables

In [1]:
import pandas as pd
import numpy as np
import pymysql

TARGET_COL = 'churn_label'
RANDOM_SEED = 42
TEST_SIZE = 0.3

from dotenv import dotenv_values
# Load the .env file
config = dotenv_values("../src/.env")


from sklearn.model_selection import GridSearchCV
from catboost import CatBoostClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import roc_auc_score, precision_score, recall_score, f1_score
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import OneHotEncoder



# Data Loading
1) Connect to SQL DB and write Query
2) Exclude NA rows from churn_label using WHERE.

In [2]:
# Define function to establish MySQL database (local) connection
def initiate_remote_connection():
    try:
        connection = pymysql.connect(
                            host=config.get('ENDPOINT'),
                            port=int(config.get('PORT')),
                            user=config.get('USERNAME'),
                            passwd=config.get('PASSWORD'),
                            db=config.get('DBNAME'),
                            cursorclass=pymysql.cursors.DictCursor
            )
        print('[+] Remote Connection Successful')
    except Exception as e:
        print(f'[+] Remote Connection Failed: {e}')
        connection = None

    return connection

# Call function and return the connection object
connection = initiate_remote_connection()

[+] Remote Connection Successful


In [3]:
def get_records(sql_query):
    try:
        with connection.cursor() as cursor:
            cursor.execute(sql_query)

        # Connection is not autocommit by default, so we must commit to save changes
        connection.commit()
        
        # Fetch all the records from SQL query output
        results = cursor.fetchall()
        
        # Convert results into pandas dataframe
        df = pd.DataFrame(results)
        
        print(f'Successfully retrieved records')
        
        return df
        
    except Exception as e:
        print(f'Error encountered: {e}')

In [4]:
SQL_CUS = """
    SELECT * from customer
    LEFT JOIN city USING(zip_code)
    LEFT JOIN account USING(customer_id)
    LEFT JOIN account_usage USING (account_id)
    LEFT JOIN churn_status USING (customer_id)
    where churn_label IS NOT NULL
"""

df = get_records(SQL_CUS)
df

Successfully retrieved records


customer_id  account_id zip_code  gender  age senior_citizen married  \
0     0013-EXCHZ  BFIN-DLMOA    93010  Female   75            Yes     Yes   
1     0014-BMAQU  AFEO-XOOCP    94558    Male   52             No     Yes   
2     0016-QLJIS  DEMQ-MFXWC    95681  Female   43             No     Yes   
3     0019-EFAEP  AIPP-VTDXJ    91942  Female   32             No      No   
4     0019-GFNTW  CJHA-SRKIB    93441  Female   39             No      No   
...          ...         ...      ...     ...  ...            ...     ...   
6986  9938-EKRGF  NAVF-FZPXC    96052  Female   58             No      No   
6987  9938-TKDGL  VKPX-MVNBC    93544    Male   38             No     Yes   
6988  9938-ZREHM  PQGJ-VYMBE    93033  Female   41             No     Yes   
6989  9961-JBNMK  SJNY-CQODU    92239    Male   79            Yes      No   
6990  9972-NKTFD  VMSC-PMRRO    95942  Female   55             No      No   

      num_dependents  area_id      city_name  ...  stream_tv  stream_movie  \
0                  0      607      Camarillo  ...        Yes            No   
1                  0      963           Napa  ...         No            No   
2                  1     1390       Sheridan  ...        Yes           Yes   
3                  0      303        La Mesa  ...        Yes            No   
4                  0      716     Los Olivos  ...         No            No   
...              ...      ...            ...  ...        ...           ...   
6986               0     1557       Lewiston  ...        Yes           Yes   
6987               3      755          Llano  ...        Yes           Yes   
6988               0      615         Oxnard  ...         No           Yes   
6989               0      395  Desert Center  ...        Yes           Yes   
6990               0     1478   Forest Ranch  ...         No            No   

      stream_music  total_monthly_fee  total_charges_quarter total_refunds  \
0               No              83.90                 267.40          0.00   
1               No              84.65                5377.80          0.00   
2              Yes              90.45                5957.90          0.00   
3               No             101.30                7261.25          0.00   
4               No              45.05                2560.10          0.00   
...            ...                ...                    ...           ...   
6986           Yes              84.45                1287.85          0.00   
6987           Yes              99.55                6668.00          0.00   
6988           Yes              72.10                2658.40         16.36   
6989            No              96.80                2030.30         10.20   
6990            No              54.65                1517.50          0.00   

     customer_status churn_label   churn_category             churn_reason  
0            Churned         Yes  Dissatisfaction      Network reliability  
1             Stayed          No             None                     None  
2             Stayed          No             None                     None  
3             Stayed          No             None                     None  
4             Stayed          No             None                     None  
...              ...         ...              ...                      ...  
6986          Stayed          No             None                     None  
6987          Stayed          No             None                     None  
6988          Stayed          No             None                     None  
6989         Churned         Yes  Dissatisfaction  Product dissatisfaction  
6990          Stayed          No             None                     None  

[6991 rows x 40 columns]

# Checking Correlation Heatmap and Boxplot of Numerical Columns

In [5]:
import plotly.express as px
numeric_df = df.select_dtypes(include='number').drop(columns = ['latitude', 'longitude'])

correlation_matrix = numeric_df.corr()
fig = px.imshow(correlation_matrix)
fig.update_layout(
    width=800,
    height=600,
    title='Correlation Heatmap'
)
fig.show()

In [6]:
import pandas as pd
import plotly.express as px

# Select all numerical columns from the DataFrame
numerical_cols = df.select_dtypes(include='number').columns.tolist()

# Create a box plot using Plotly
fig = px.box(df, y=numerical_cols)

# Show the plot
fig.show()


In [7]:

import plotly.subplots as sp
import plotly.graph_objects as go

# Calculate the mean of tenure_months, total_monthly_fee, total_charges_quarter, and total_long_distance_fee for each age group
age_mean = df.groupby('age').agg({
    'tenure_months': 'mean',
    'total_monthly_fee': 'mean',
    'total_charges_quarter': 'mean'
}).reset_index()

# Create subplots using Plotly
fig = sp.make_subplots(rows=1, cols=3, subplot_titles=('Tenure Months', 'Total Monthly Fee', 'Total Charges Quarter', 'Total Long Distance Fee'))

# Add the first subplot for tenure_months
fig.add_trace(go.Bar(x=age_mean['age'], y=age_mean['tenure_months'], marker_color='steelblue'), row=1, col=1)

# Add the second subplot for total_monthly_fee
fig.add_trace(go.Bar(x=age_mean['age'], y=age_mean['total_monthly_fee'], marker_color='indianred'), row=1, col=2)

# Add the third subplot for total_charges_quarter
fig.add_trace(go.Bar(x=age_mean['age'], y=age_mean['total_charges_quarter'], marker_color='lightsalmon'), row=1, col=3)


# Customize the layout
fig.update_layout(
    title='Mean Values by Age',
    xaxis=dict(title='Age'),
    showlegend=False
)

# Show the plot
fig.show()



### Observations: 
1) Senior Citizens on avg use spend more per month. (Unexpected)
2) Tenure Months roughly same for all age groups.

# Data Preprocessing
1) Drop churn_category, churn_reason, customer_status

2) Binarize churn_label


In [8]:
df = df.drop(columns = ['churn_category', 'churn_reason', 'customer_status'])
df = df.dropna()

def binarize_column(df, col_name):
    def binarize(value):
        if value in ['Yes']:
            return 1
        elif value in ['No']:
            return 0
    df[col_name] = df[col_name].apply(binarize)
    return df

df = binarize_column(df, 'churn_label')
df['churn_label'].head(10)
        

0    1
1    0
2    0
3    0
4    0
5    0
6    0
7    0
8    0
9    0
Name: churn_label, dtype: int64

# Feature Engineering

1. Added refund ratio:
   
   ```python
   refund_ratio_qtr = np.log1p(df['total_refunds']) - np.log1p(df['total_charges_quarter'])

2. Added total long distance fee per dependant

   ```python
   total_long_distance_fee_per_dependant = np.log1p(df['total_long_distance_fee']) - np.log1p(df['num_dependents'])

3. Added total GB downloaded

   ```python
   df['total_gb_downloaded'] = df['avg_gb_download_monthly'] * df['tenure_months']



In [9]:
# Calculate 'refund_ratio_qtr' feature
df['refund_ratio_qtr'] = np.log1p(df['total_refunds']) - np.log1p(df['total_charges_quarter'])

# Calculate 'total_long_distance_fee_per_dependant' feature
df['total_long_distance_fee_per_dependant'] = np.log1p(df['total_long_distance_fee']) - np.log1p(df['num_dependents'])

# Calculate 'total_gb_downloaded' feature
df['total_gb_downloaded'] = df['avg_gb_download_monthly'] * df['tenure_months']

df.head(10)

customer_id  account_id zip_code  gender  age senior_citizen married  \
0  0013-EXCHZ  BFIN-DLMOA    93010  Female   75            Yes     Yes   
1  0014-BMAQU  AFEO-XOOCP    94558    Male   52             No     Yes   
2  0016-QLJIS  DEMQ-MFXWC    95681  Female   43             No     Yes   
3  0019-EFAEP  AIPP-VTDXJ    91942  Female   32             No      No   
4  0019-GFNTW  CJHA-SRKIB    93441  Female   39             No      No   
5  0020-INWCK  CDSG-JLJOW    93286  Female   58             No     Yes   
6  0036-IHMOT  EDRJ-TSFHQ    93648  Female   37             No     Yes   
7  0052-DCKON  GGNP-KVFOQ    90063    Male   28             No     Yes   
8  0052-YNYOT  BTJY-YSXTR    92231  Female   28             No      No   
9  0060-FUALY  AUVC-CVWLX    90003  Female   60             No     Yes   

   num_dependents  area_id    city_name  ...  stream_tv  stream_movie  \
0               0      607    Camarillo  ...        Yes            No   
1               0      963         Napa  ...         No            No   
2               1     1390     Sheridan  ...        Yes           Yes   
3               0      303      La Mesa  ...        Yes            No   
4               0      716   Los Olivos  ...         No            No   
5               2      685     Woodlake  ...         No           Yes   
6               3      803      Parlier  ...        Yes           Yes   
7               0       53  Los Angeles  ...        Yes           Yes   
8               0      391     Calexico  ...         No            No   
9               0        3  Los Angeles  ...        Yes            No   

   stream_music  total_monthly_fee  total_charges_quarter total_refunds  \
0            No              83.90                 267.40          0.00   
1            No              84.65                5377.80          0.00   
2           Yes              90.45                5957.90          0.00   
3            No             101.30                7261.25          0.00   
4            No              45.05                2560.10          0.00   
5           Yes              95.75                6849.40          0.00   
6           Yes             103.70                5656.75          0.00   
7           Yes             115.80                7942.15          0.00   
8            No              20.55                1343.40         30.53   
9            No              94.75                5597.65          0.00   

  churn_label refund_ratio_qtr total_long_distance_fee_per_dependant  \
0           1        -5.592478                              3.141563   
1           0        -8.590221                              6.706226   
2           0        -8.692641                              6.830280   
3           0        -8.890445                              5.093750   
4           0        -7.848192                              0.000000   
5           0        -8.832062                              6.470005   
6           0        -8.640782                              6.178048   
7           0        -8.980065                              7.968949   
8           0        -3.752764                              7.346036   
9           0        -8.630281                              6.875242   

  total_gb_downloaded  
0                  33  
1                 441  
2                 910  
3                1152  
4                1064  
5                 852  
6                3135  
7                2706  
8                   0  
9                 826  

[10 rows x 40 columns]

# Choosing Features
1. Drop unnecessary features and split dataset into X, y.


In [11]:
# Including only a few features for now.
excluded_cols = [TARGET_COL, 'customer_id', 'account_id', 'zip_code', 'area_id', 'latitude', 'longitude']

# Split dataset into model input features and labels (aka target variable)
X = df.drop(columns=excluded_cols)
y = df[TARGET_COL]

# Model Evaluation
1) CatBoost 

2) RandomForest

In [12]:
# Extract categorical columns programmatically

cat_features = list(X.select_dtypes(include='object').columns)
print(cat_features)

['gender', 'senior_citizen', 'married', 'city_name', 'has_internet_service', 'internet_type', 'has_unlimited_data', 'has_phone_service', 'has_multiple_lines', 'has_premium_tech_support', 'has_online_security', 'has_online_backup', 'has_device_protection', 'contract_type', 'paperless_billing', 'payment_method', 'stream_tv', 'stream_movie', 'stream_music']


## Train CatBoost Classifier

In [13]:
model = CatBoostClassifier()
param_grid = {
    'iterations': [100, 200, 300],
    'depth': [4, 6],
    'learning_rate': [0.01, 0.05, 0.1],
    'l2_leaf_reg': [1, 3],
}

grid_search = GridSearchCV(model, param_grid, cv=5, scoring='roc_auc') #Optimize for ROC_AUC
grid_search.fit(X, y, cat_features=cat_features, verbose=True)

print("Best Parameters:", grid_search.best_params_)

0:	learn: 0.6843259	total: 189ms	remaining: 18.7s
1:	learn: 0.6771353	total: 209ms	remaining: 10.2s
2:	learn: 0.6687419	total: 229ms	remaining: 7.41s
3:	learn: 0.6604800	total: 254ms	remaining: 6.09s
4:	learn: 0.6523070	total: 274ms	remaining: 5.2s
5:	learn: 0.6448132	total: 294ms	remaining: 4.6s
6:	learn: 0.6367107	total: 314ms	remaining: 4.17s
7:	learn: 0.6307299	total: 335ms	remaining: 3.86s
8:	learn: 0.6244744	total: 360ms	remaining: 3.64s
9:	learn: 0.6189926	total: 389ms	remaining: 3.5s
10:	learn: 0.6133142	total: 419ms	remaining: 3.39s
11:	learn: 0.6082259	total: 455ms	remaining: 3.34s
12:	learn: 0.6027885	total: 489ms	remaining: 3.27s
13:	learn: 0.5975076	total: 526ms	remaining: 3.23s
14:	learn: 0.5928856	total: 567ms	remaining: 3.21s
15:	learn: 0.5867660	total: 605ms	remaining: 3.18s
16:	learn: 0.5803221	total: 656ms	remaining: 3.2s
17:	learn: 0.5748201	total: 725ms	remaining: 3.3s
18:	learn: 0.5704202	total: 777ms	remaining: 3.31s
19:	learn: 0.5661264	total: 826ms	remaining: 3

### Best Parameters: {'depth': 6, 'iterations': 200, 'l2_leaf_reg': 3, 'learning_rate': 0.05}

In [14]:
import pickle

# Assigning grid_search object with best_params_ to a variable.
best_params = grid_search.best_params_

# Define the file path to save the pickle file
file_path = '../model/catboost_best_params.pkl'

# Save the best_params object to a pickle file
with open(file_path, 'wb') as f:
    pickle.dump(best_params, f)

In [15]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=TEST_SIZE, random_state=RANDOM_SEED)

best_cat_model = CatBoostClassifier(**grid_search.best_params_, random_state=RANDOM_SEED)
best_cat_model.fit(X_train, y_train, cat_features=cat_features, verbose=False)
y_pred = best_cat_model.predict(X_test)
y_pred_proba = best_cat_model.predict_proba(X_test)[:,1]

# Evaluate the model with various metrics
cat_roc_auc_score = roc_auc_score(y_test, y_pred_proba)
print("Cat AUC:", roc_auc_score(y_test, y_pred_proba))
print("Cat Precision Score:", precision_score(y_test, y_pred))
print("Cat Recall Score:", recall_score(y_test, y_pred))
print("Cat F1 Score:", f1_score(y_test, y_pred))

Cat AUC: 0.9186409361041714
Cat Precision Score: 0.7760869565217391
Cat Recall Score: 0.65625
Cat F1 Score: 0.7111553784860559


### Optimizing Threshold using f1 Score, plotting it, and saving as pkl file.

In [18]:
import numpy as np
import plotly.graph_objects as go

# Obtain optimal threshold using F1 score
threshold_values = np.arange(0.1, 1.0, 0.1)
f1_scores = []
for threshold in threshold_values:
    y_pred_threshold = (y_pred_proba >= threshold).astype(int)
    f1_scores.append(f1_score(y_test, y_pred_threshold))

optimal_threshold = threshold_values[np.argmax(f1_scores)]

# Plotting the F1 score at different thresholds using Plotly
fig = go.Figure(data=go.Scatter(x=threshold_values, y=f1_scores, mode='lines+markers'))
fig.update_layout(
    title="F1 Score at Different Thresholds for CatBoost Classifier",
    xaxis_title="Threshold",
    yaxis_title="F1 Score",
    showlegend=False
)
fig.show()

print("Optimal Threshold:", optimal_threshold)

# Save the optimal threshold to a pickle file
with open('../model/optimal_threshold.pkl', 'wb') as file:
    pickle.dump(optimal_threshold, file)

Optimal Threshold: 0.30000000000000004


## Train Random Forest Classifier

In [38]:
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import OneHotEncoder

# Apply one-hot encoding to categorical features
encoder = OneHotEncoder(handle_unknown='ignore')
X_encoded = encoder.fit_transform(X[cat_features])

model = RandomForestClassifier()
param_grid = { #Simple example, need to add more parameters.
    'n_estimators': [100, 200, 300],
    'max_depth': [1, 5, 10],
    'min_samples_split': [2, 5, 10],
    'min_samples_leaf': [1, 2, 4]
}

grid_search = GridSearchCV(model, param_grid, cv=5, scoring='roc_auc')
grid_search.fit(X_encoded, y)
print("Best Parameters:", grid_search.best_params_)

X_train, X_test, y_train, y_test = train_test_split(X_encoded, y, test_size=TEST_SIZE, random_state=RANDOM_SEED)

best_rf_model = RandomForestClassifier(**grid_search.best_params_, random_state=RANDOM_SEED)
best_rf_model.fit(X_train, y_train)
y_pred = best_rf_model.predict(X_test)
y_pred_proba = best_rf_model.predict_proba(X_test)[:,1]

rf_roc_auc_score = roc_auc_score(y_test, y_pred_proba)
print("AUC:", roc_auc_score(y_test, y_pred_proba))
print("Precision Score:", precision_score(y_test, y_pred))
print("Recall Score:", recall_score(y_test, y_pred))
print("F1 Score:", f1_score(y_test, y_pred))

Best Parameters: {'max_depth': 10, 'min_samples_leaf': 1, 'min_samples_split': 2, 'n_estimators': 100}
AUC: 0.8670609291013703
Precision Score: 0.8813559322033898
Recall Score: 0.19117647058823528
F1 Score: 0.3141993957703927


# Choosing best model and saving model

In [40]:
import pickle

if rf_roc_auc_score > cat_roc_auc_score:
    print("RF Model chosen due to higher roc_auc_score.")
    final_model_rf = best_rf_model.fit(X, y)
    # Save the model
    with open('../model/rf_model.pkl', 'wb') as f:
        pickle.dump(final_model_rf, f)
        print("Random Forest Model saved in model folder.")
        
else:
    print("CatBoost Model chosen due to higher roc_auc_score.")
    final_model_cat = best_cat_model.fit(X, y, cat_features=cat_features, verbose=False)
    # Save the model
    with open('../model/catboost_model.pkl', 'wb') as f:
        pickle.dump(final_model_cat, f)
        print("CatBoost Model saved in model folder.")

CatBoost Model chosen due to higher roc_auc_score.
CatBoost Model saved in model folder.
